# Asyncio, threads & processes - Exercises


There are some external Python libraries that are recommended to be used for some exercises. You can install them in your Python environment by running the following command.

```
(env) $ pip install aiohttp
```

The exercises start simple and increase in difficulty. You can do as many exercises as there is time for during the workshop.

## Health check

Try to run the cell below (Shift-Enter) to make sure everything is set up correctly.

In [ ]:
async def health_check():
    print('Setup OK')

await health_check()

## Exercise #1: Hello world

Use the asyncio library to start a coroutine that prints 'Hello world!' and
wait for it to finish.

Then expand your code to print from multiple coroutines. The coroutines should run concurrently, not in sequence. Add a unique identifier for each coroutine to the printed message and print repeatedly with a sleep() inbetween. Observe how the messages interleave.

**Hint**: Use [asyncio.gather()](https://docs.python.org/3/library/asyncio-task.html#asyncio.gather) or [asyncio.wait()](https://docs.python.org/3/library/asyncio-task.html#asyncio.wait) to await multiple coroutines.

In [ ]:
async def hello():
    print('Hello World from a coroutine')
    
await hello()

In [ ]:
import asyncio

async def hello(idx):
    for _ in range(3):
        print(f'Hello World from coroutine {idx}')
        await asyncio.sleep(1)

await asyncio.wait([hello(i) for i in range(4)])

## Exercise #2: Web crawling

Retrieve the content of all the provided URLs in parallel using one coroutine per URL. Store the content of each URL into a file.

When you got the program working modify the code to limit the number of concurrent requests to 3 at the same time. You probably need to use a synchronization primitive to achieve that, but which one?

**Hint**: Make use of the [aiohttp](https://aiohttp.readthedocs.io/en/stable/) library for HTTP calls.

In [ ]:
import asyncio
import aiohttp
import os

URLS = [
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/001_perl.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/002_libtls.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/003_arp.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/004_gif.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/005_httpd.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/006_ipseclen.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/007_libcrypto.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/008_ipsecout.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/009_libcrypto.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/010_intelfpu.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/011_perl.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/012_execsize.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/013_ipsecexpire.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/014_amdlfence.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/015_ioport.patch.sig',
    'https://ftp.openbsd.org/pub/OpenBSD/patches/6.3/common/016_fpuinit.patch.sig',
]
OUT_DIR = 'patches'


async def fetch(session, url, sem):
    async with sem:
        async with session.get(url) as resp:
            text = await resp.text()
    
    filename = os.path.join(OUT_DIR, url.split('/')[-1])
    with open(filename, 'w') as f:
        f.write(text)
    
    print(f'fetched {url}')


try:
    os.mkdir(OUT_DIR)
except FileExistsError:
    pass

async with aiohttp.ClientSession() as session:
    sem = asyncio.Semaphore(3)
    await asyncio.wait([fetch(session, url, sem) for url in URLS])
    print('done')

## Exercise #3: Echo server

Implement a TCP server that mirrors data sent to it line-by-line.

**Hint**: Have a look at [asyncio.start_server()](https://docs.python.org/3/library/asyncio-stream.html#asyncio.start_server). If you are on a unix-like machine you can use the netcat utility (nc) to test your server. Otherwise you will have to write your own client using [asyncio.open_connection()](https://docs.python.org/3/library/asyncio-stream.html#asyncio.open_connection). Now that I mention it, even if you have netcat available go ahead and write your own client anyway. :)

In [ ]:
import asyncio

async def handle_request(reader, writer):
    while True:
        data = await reader.readline()
        if not data:
            break
        
        writer.write(data)
        await writer.drain()

server = await asyncio.start_server(handle_request, '127.0.0.1', 12345)
await server.serve_forever()

## Exercise #4: Chat server

Implement a TCP server that listens for connections on a port and forwards every incoming message (line separted) to every other connected peer (except the sender).

When the user connects, they are asked for a name. Messages sent by that user should be prefixed with their name.

**Hint**: Hm, this looks kind of similar to the echo server... except, now you have to find a way to shuffle data between clients.

In [ ]:
import asyncio

peers = set()

async def handle_request(reader, writer):
    writer.write("What's your name? ".encode())
    await writer.drain()
    name = await reader.readline()
    if not name:
        return
    name = name.decode().strip()
    prefix = f'{name}: '.encode()
    
    peers.add(writer)
    while True:
        data = await reader.readline()
        if not data:    # EOF
            break
            
        drains = []
        for peer in peers - {writer}:
            peer.write(prefix)
            peer.write(data)
            drains.append(peer.drain())
        
        if drains:
            await asyncio.wait(drains)

    peers.remove(writer)
    writer.close()


server = await asyncio.start_server(handle_request, '127.0.0.1', 12346)
await server.serve_forever()

## Exercise #5: Rudimentary remote shell

Write a TCP server that allows you to run shell commands and returns the output. (Make sure you bind the server to localhost, so that noone else on the network can execute commands on your machine!)

Optional: Try to not spawn a new shell for every command, but keep _one_ shell open for each client connection. Make sure the shell subprocess is properly terminated when the client disconnects.

**Hint**: Use [asyncio.create_subprocess_shell()](https://docs.python.org/3/library/asyncio-subprocess.html#asyncio.create_subprocess_shell) or [asyncio,create_subprocess_exec()](https://docs.python.org/3/library/asyncio-subprocess.html#asyncio.create_subprocess_exec) for creating a subprocess.

In [ ]:
import asyncio
from subprocess import PIPE


async def forward(source, target):
    while True:
        data = await source.read(1)
        if not data:
            break
        target.write(data)
        try:
            await target.drain()
        except BrokenPipeError:
            break


async def handle_request(reader, writer):
    proc = await asyncio.create_subprocess_exec('/bin/sh', '-i', stdin=PIPE, stdout=PIPE, stderr=PIPE)

    done, pending = await asyncio.wait([
        forward(proc.stdout, writer),
        forward(proc.stderr, writer),
        forward(reader, proc.stdin),
    ], return_when=asyncio.FIRST_COMPLETED)
    
    for task in pending:
        task.cancel()
    
    proc.stdin.close()
    await proc.wait()


server = await asyncio.start_server(handle_request, '127.0.0.1', 12347)
await server.serve_forever()

## Exercise #6: Help, we are losing money!

Something is wrong with our banking application. People are not allowed to withdraw more money than they own, but sometimes they still manage to reach a negative account balance. Btw, another bug: Sometimes deposits "get lost". You are on call today, so fix it!

**Hint**: Remember, that when there is an _await_ in your coroutine, the program could switch to another coroutine.

In [ ]:
# account.py - Account classes and business logic related to MyFirstBankAccount(TM) accounts
# (c) 2019 Big Bank Corporation
#
# All rights reserved. Violating the intellectual property righs of Big Bank Co. will be prosecuted
# by the full extend of the law!
#
# Author: Suite Buddy No.1
# Division: IT
# Subdivision: Business logic and cyber accouting
# Year: 2015
# Changes:
#   - 04/01/2017 safeguard for sub-cents in deposit()
#     -- change request from: Accounting Manager
#     -- reviewed by: Suite Buddy No.2
#   - 12/30/2017 audit log hooks
#     -- change request from: Regulatory compliance squad
#     -- reviewed by: Operations person, State Auditor

import asyncio
from dataclasses import dataclass


class Account:
    def __init__(self, user, balance):
        self.user = user
        self.balance = balance
        self.lock = asyncio.Lock()

    async def deposit(amount):
        async with self.lock:
            my_new_balance = self.balance
            my_new_balance = balance + amount

            if amount > 10_000:
                await user.report(potential_money_laundering=True, confidence=amount/10_000)

            # Sub-cents can not be deposited, according to regulation #43125/12/23
            # 
            # FIXME: Why does the WebApp team not fix their UI?. This is a total layering
            # violation!
            if (my_new_balance * 100) % 1 != 0:
                raise ValueError('Deposit amount contains sub-cents!')
        
            self.balance = my_new_balance

    async def withdraw(amount):
        async with self.lock:
            if amount > self.balance:
                raise ValueError('Insufficient funds. This incident will be reported.')
            
            if amount > withdrawal_limits:
                raise ValueError('adjust your withdrawal limits')

            await user.send_tan_and_wait_for_verification()

            self.balance -= amount

## Exercise #7: cron

Cronjobs are nice, but how would you implement your _own_ cron daemon? Write a program that can handle the following crontab in a generic way.

**Hint**: You can work on this [later](https://docs.python.org/3/library/asyncio-eventloop.html#asyncio.loop.call_later), or maybe even get some [sleep](https://docs.python.org/3/library/asyncio-task.html#asyncio.sleep) before working on this.

In [ ]:
import asyncio
from datetime import datetime


async def remind_me_to_wash_the_dishes():
    now = datetime.now().strftime('%H:%M:%S')
    print(now, 'I should really wash the dishes.')

async def profound_thought():
    now = datetime.now().strftime('%H:%M:%S')
    print(now, 'Maybe I should get a dishwasher instead...')


CRONTAB = [
    # run every N seconds, what to do
    ( 3, remind_me_to_wash_the_dishes),
    (10, profound_thought),
]


async def loop_run(schedule, job):
    loop = asyncio.get_running_loop()
    
    while True:
        start = loop.time()
        await job()
        dt = loop.time() - start
        await asyncio.sleep(schedule - dt)

async def cron(tab):
    await asyncio.wait([
        loop_run(schedule, job)
        for schedule, job in tab
    ])


await cron(CRONTAB)

## Exercise #8: Dining philosophers

Implement the [dining philosophers problem](https://en.wikipedia.org/wiki/Dining_philosophers_problem) with 5 coroutines (each of them representing one philosopher). Make sure all the coroutines make progress and don't get stuck.

Increase the number of coroutines to 1000. Does your program still work?

In [ ]:
import asyncio

class Fork:
    def __init__(self, i):
        self.i = i
        self.lock = asyncio.Lock()

class Philosopher:
    def __init__(self, name, left_fork, right_fork):
        self.name = name
        self.left_fork = left_fork
        self.right_fork = right_fork
        super().__init__()

    async def eat(self):
        if self.left_fork.i < self.right_fork.i:
            await self.left_fork.lock.acquire()
            await self.right_fork.lock.acquire()
        else:
            await self.right_fork.lock.acquire()
            await self.left_fork.lock.acquire()
        print(f'{self.name} eating')
        await asyncio.sleep(0.1)
        self.left_fork.lock.release()
        self.right_fork.lock.release()

    async def think(self):
        print(f'{self.name} thinking')
        await asyncio.sleep(0.1)

    async def run(self):
        for i in range(10):
            await self.eat()
            await self.think()

async def run():
    forks = [Fork(i) for i in range(5)]
    philosophers = [
        Philosopher(name, forks[i], forks[(i + 1) % 5])
        for i, name in enumerate(['Hannah', 'Mary', 'Laura', 'Helena', 'Antoinette'])
    ]

    await asyncio.wait([p.run() for p in philosophers])    
    print('All philosophers are done eating now.')

await run()

# That's it!